In [81]:
import numpy as np
import pandas as pd
from bs4 import BeautifulSoup
import webbrowser
import io
import urllib
import urllib.request
import urllib.error
from lxml import html
import requests
from collections import OrderedDict
import json
import argparse
import re
import sys
from selenium import webdriver
import scrapy
from scrapy import Selector
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By

In [91]:
def display(content, filename='output.html'):
    with open(filename, 'wb') as f:
        f.write(content)
        webbrowser.open(filename)

################################
def get_soup(session, url, show=False):
    r = session.get(url)
    if show:
        display(r.content, 'temp.html')

    if r.status_code != 200: # not OK
        print('[get_soup] status code:', r.status_code)
    else:
        return BeautifulSoup(r.text, 'html.parser')

#################################    
def post_soup(session, url, params, show=False):
    '''Read HTML from server and convert to Soup'''

    r = session.post(url, data=params)
    
    if show:
        display(r.content, 'temp.html')

    if r.status_code != 200: # not OK
        print('[post_soup] status code:', r.status_code)
    else:
        return BeautifulSoup(r.text, 'html.parser')

##################################    
def get_reviews_ids(soup):
    items = soup.find_all('div', attrs={'data-reviewid': True})
    if items:
        reviews_ids = [x.attrs['data-reviewid'] for x in items][::2]
        print('[get_reviews_ids] data-reviewid:', reviews_ids)
        return reviews_ids

##################################
def parse(session, url):
    '''Get number of reviews and start getting subpages with reviews'''

    print('[parse] url:', url)

    soup = get_soup(session, url)

    if not soup:
        print('[parse] no soup:', url)
        return

    num_reviews = soup.find('span', class_='reviews_header_count').text # get text
    num_reviews = num_reviews[1:-1] 
    num_reviews = num_reviews.replace(',', '')
    num_reviews = int(num_reviews) # convert text into integer
    print('[parse] num_reviews ALL:', num_reviews)

    url_template = url.replace('.html', '-or{}.html')
    print('[parse] url_template:', url_template)

    items = []

    offset = 0

    while(True):
        subpage_url = url_template.format(offset)

        subpage_items = parse_reviews(session, subpage_url)
        if not subpage_items:
            break

        items += subpage_items

        if len(subpage_items) < 5:
            break

        offset += 5

    return items
    
    

##################################
def parse_reviews(session, url):
    '''Get all reviews from one page'''

    print('[parse_reviews] url:', url)

    soup =  get_soup(session, url)

    if not soup:
        print('[parse_reviews] no soup:', url)
        return

    hotel_name = soup.find('h1', id='HEADING').text

    reviews_ids = get_reviews_ids(soup)
    if not reviews_ids:
        return

    soup = get_more(session, reviews_ids)

    if not soup:
        print('[parse_reviews] no soup:', url)
        return

    items = []

    for idx, review in enumerate(soup.find_all('div', class_='reviewSelector')):

        badgets = review.find_all('span', class_='badgetext')
        if len(badgets) > 0:
            contributions = badgets[0].text
        else:
            contributions = '0'

        if len(badgets) > 1:
            helpful_vote = badgets[1].text
        else:
            helpful_vote = '0'
        user_loc = review.select_one('div.userLoc strong')
        if user_loc:
            user_loc = user_loc.text
        else:
            user_loc = ''
            
        bubble_rating = review.select_one('span.ui_bubble_rating')['class']
        bubble_rating = bubble_rating[1].split('_')[-1]

        item = {
            'review_date': review.find('span', class_='ratingDate')['title'], # 'ratingDate' instead of 'relativeDate',
            'experience_date': review.find('span', class_='prw_rup'),
            'review_body': review.find('p', class_='partial_entry').text,
            'rating': review.select_one('span.ui_bubble_rating')['class'][1],
            'review_title': review.find('span', class_='noQuotes').text
        }

        items.append(item)
        print('\n--- review ---\n')
        for key,val in item.items():
            print(' ', key, ':', val)

    print()

    return items


##################################
def get_more(session, reviews_ids):
    url = 'https://www.tripadvisor.com/OverlayWidgetAjax?Mode=EXPANDED_HOTEL_REVIEWS_RESP&metaReferer=Hotel_Review'
    payload = {
        'reviews': ','.join(reviews_ids), # ie. "577882734,577547902,577300887",
        #'contextChoice': 'DETAIL_HR', # ???
        'widgetChoice': 'EXPANDED_HOTEL_REVIEW_HSX', # ???
        'haveJses': 'earlyRequireDefine,amdearly,global_error,long_lived_global,apg-Hotel_Review,apg-Hotel_Review-in,bootstrap,desktop-rooms-guests-dust-en_US,responsive-calendar-templates-dust-en_US,taevents',
        'haveCsses': 'apg-Hotel_Review-in',
        'Action': 'install',
    }
    soup = post_soup(session, url, payload)

    return soup


##################################
def scrape(url, lang='ALL'):
    reviews = []
    # create session to keep all cookies (etc.) between requests
    session = requests.Session()
    session.headers.update({
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; WOW64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/77.0.3865.120 Safari/537.36',
    })
    items = parse(session, url + '?filterLang=' + lang)
    
    #for item in items:
     #   if item not in reviews:
      #      reviews.append(item)
    return items

In [92]:
review_list2=[]
for i in range(10, 20, 10):      
    url = "https://www.tripadvisor.com/Attraction_Review-g187791-d3167242-Reviews-or{}-The_Roman_Guy-Rome_Lazio.html".format(i)
    reviews = parse_reviews(session, url)
    review_list.append(reviews)
review_list2

[parse_reviews] url: https://www.tripadvisor.com/Attraction_Review-g187791-d3167242-Reviews-or10-The_Roman_Guy-Rome_Lazio.html
[get_reviews_ids] data-reviewid: ['720550493', '720402273', '720354675', '720324416', '720315220', '720221371', '720117817', '720050388', '720041738', '720018711']

--- review ---

  review_date : October 22, 2019
  experience_date : None
  review_body : This was our 2nd tour using The Roman Guy company (1st was early morning Vatican City and Sistine Chapel which was also fantastic). It was well ran, organised, informative and as described on their website. Sylvia, our tour guide, was enthusiastic, patient and very helpful from start to finish. I would highly recommend the extra $$ to enhance your trip to Rome and get the most out of these wonderful, historical sites.
  rating : bubble_50
  review_title : Excellent Tour

--- review ---

  review_date : October 22, 2019
  experience_date : None
  review_body : Our guide Serena was great and informative. Our only

[]

In [74]:
review_list=[]
for i in range(10, 4220, 10):      
    url = "https://www.tripadvisor.com/Attraction_Review-g187791-d3167242-Reviews-or{}-The_Roman_Guy-Rome_Lazio.html".format(i)
    reviews = parse_reviews(session, url)
    review_list.append(reviews)
review_list

[parse_reviews] url: https://www.tripadvisor.com/Attraction_Review-g187791-d3167242-Reviews-or10-The_Roman_Guy-Rome_Lazio.html
[get_reviews_ids] data-reviewid: ['720402273', '720354675', '720324416', '720315220', '720221371', '720117817', '720050388', '720041738', '720018711', '719948582']

--- review ---

  review_date : October 22, 2019
  review_body : Our guide Serena was great and informative. Our only complaint had nothing to do with Serena or The Roman Guy, it was the venue itself. On many photos the colosseum appears well lit during the after hours tour, but it was not. It was difficult to make anything out from the various vantage points that we were at. There was quite a bit of walking and many stairs involved, but we’re chubby and needed the exercise. I can’t fault anyone but the keepers of the colosseum itself for the poor illumination. It did make it a little disappointing, but it was still nice to see what we did with essentially no one around us. I would certainly book wi

[get_reviews_ids] data-reviewid: ['719582613', '719538562', '719537323', '719395063', '719149816', '719146223', '719052612', '719041684', '718796022', '718738276']

--- review ---

  review_date : October 19, 2019
  review_body : A group of 6 seasoned travellers, we were completely blown away by the professionalism and attention to detail of the Roman Guy. We did 2 private tours, the Colosseum, Palatine Hill, Forum tour on the first day and the Skip the queue private tour of the Vatican, Sistine Chapel, St Peters the next day. I had done these tours with another company before about 7 years ago but within 15 minutes of these tours I felt more informed and more engaged than after 3.5 hours on the previous tours. Special mention must go to Serena and Sara, our 2 guides, who were beyond amazing - absolute experts in not only their subject matter but also in maintaining the group's excitement and engagement going for 3.5 hours which is no mean feat. For sure the best guides we have ever co

[get_reviews_ids] data-reviewid: ['718437303', '718385896', '718329343', '718323541', '718298792', '718278061', '718208619', '718194298', '718091770', '718055834']

--- review ---

  review_date : October 14, 2019
  review_body : Great tour, pricey but get to see much of Rome! Geat tour guide, learnt a lot, recommend for everyone!
  rating : bubble_50
  review_title : Rome

--- review ---

  review_date : October 14, 2019
  review_body : My fiancé and I did this tour with Loretta. She was friendly, knowledgeable, and made the tour enjoyable. The tour was the perfect size (around 12 people), we were able to cut all lines, and the tour was worth every penny!
  rating : bubble_50
  review_title : Excellent

--- review ---

  review_date : October 14, 2019
  review_body : Naomi was our tour guide and she did a great job of explaining the highlights of the museum, St. Peters, and the Sistine Chapel. She is quiet but competent and led the tour great. The only slightly negative thing is that 

[get_reviews_ids] data-reviewid: ['717718453', '717716725', '717709790', '717674870', '717632276', '717535489', '717452284', '717359031', '717333099', '717316598']

--- review ---

  review_date : October 12, 2019
  review_body : The booking process and instructions made it easy to meet the guide at the designated point - who cant find the Realto Bridge in Venice??? Our Guide was very amiable and being a long term resident was very knowlegeable. We were plied with our choice of Spritz or wine over the lunch time tour and enjoyed a respectable pasta lunch - not too large after a couple of Bacarri visits. we were in Venice for a two week trip and were familiar with the are we visisted on the tour but enjoyed it immensely.Receommended for those on a limited time visit as it provides excellent insight into the city and its culture.Grazie Mille e Buona Giornata
  rating : bubble_40
  review_title : Easy walking, short tour of Venetian Food/wine culture

--- review ---

  review_date : Octob

[get_reviews_ids] data-reviewid: ['717036201', '716961802', '716956195', '716915217', '716904431', '716898949', '716892743', '716830736', '716766870', '716647653']

--- review ---

  review_date : October 10, 2019
  review_body : Highly recommend this tour guide group. Pricing and value are excellent. The guides are fantastic. I came across their You Tube Videos. Watch them, very informative and funny. On line staff is quick and responsive with booking issues or questions. We took 3 tours. Trastevere food Tour, Colosseum early entry and floor access and the Sistine Chapel Vatican museum tour. Each one excellent. The Vatican extremely crowded!!! My favorite was the food tour. Our guide Fiona was wonderful and engaging. It felt like we were hanging out with a long time friend. Fiona was fantastic !!! 
  rating : bubble_50
  review_title : Best Tour company 

--- review ---

  review_date : October 10, 2019
  review_body : We were fortunate enough to pick "The Roman Guy" for our Colesseum

...

[get_reviews_ids] data-reviewid: ['165380524', '165362225', '165101721', '164684545', '164167150', '163730758', '163304401', '163078164', '162730939', '161722291']

--- review ---

  review_date : June 26, 2013
  review_body : We used Sean of The Roman Guy for a tour of the Colosseum, and the Forum. It was superb. Sean offered us insight that we never could have gotten another way. He is a dual citizen of the United States, and Italy, and as such, he is able to act as a bridge between the cultures, translating the hitherto inexplicable. And even though we only toured the Colosseum and the Forum with him, he was very happy to chat with us about Italy in general, and help us better understand the country and the people we were interacting with. He brought Rome--both ancient and modern--to life and helped us understand the Romans in a very real and human light. I left feeling like I knew who they were, and why they thought as they did. The only regret I have is that we didn't use this com

[get_reviews_ids] data-reviewid: ['160597261', '160349538', '160059778', '159348683', '159177026', '159142716', '158945277', '158853552', '158784313', '157604221']

--- review ---

  review_date : May 13, 2013
  review_body : We went on a tour with Sean inside the Forum Romanum. Sean made the tour fun, interesting, fact-filled. I appriciated that he speaks American fluently compared to other tour guides who speaks with an foreign accent that makes it hard to follow. The best tour I have ever been on. I will definatly use him the next time I'm in Rome and I can highly recommended him!
  rating : bubble_50
  review_title : Highly recommended!

--- review ---

  review_date : May 11, 2013
  review_body : There is no way to convey how much we enjoyed and appreciate Sean's tour. After becoming ill and having to cancel all of our tours and cut our 3 days in Rome to 1 The Roman Guy saved the trip! I called The Roman Guy on our only day in Rome and explained my situation. Even though it was ra

[get_reviews_ids] data-reviewid: ['157514296', '153861246', '152522932', '152521530', '149210502', '148849187', '145975160', '145272543', '145195271', '144769774']

--- review ---

  review_date : April 12, 2013
  review_body : Both myself and my girfriend met Sean at the entrance to Palatine Hill in Rome..we joined him for a tour. It was very enjoyable and Sean explained the history of the place to the group while keeping everyone interested. Top marks to Sean and his company. If you are in Rome, definitely go on The Roman Guys Tours /Guided Walks. A must, and well worth it! 
  rating : bubble_50
  review_title : The Roman Guy -- a must!!

--- review ---

  review_date : March 6, 2013
  review_body : we loved the city and we loved our guide. Brandon is a true great roman guy. he took care of us with the right amount of discretion and nearness. we can recommend a trip to rome, and we can recommend brandon to organzie your trip to that beautiful city.
  rating : bubble_50
  review_title

  review_body : Brandon, "the Roman Guy" was highly recommended to us through friends who recently toured Italy. The 14 of us decided to set up a tour of Rome before going on a cruise. We met Brandon and he arranged the Vatican Tour on our first day. It was a great day; we were picked up by a private van, we didn't have to purchase our tickets, everything was pre-arranged. At the end of the tour, Brandon made reservations for us at a great restaurant in Rome. Day 2, Brandon arranged us to tour the rest of Rome in golf carts. It was a blast! We got to see the fabulous city of Rome, in just a few hours. Our 2 days in Rome was a memorable experience. We loved our tour of Rome so much we decided instead of using the cruise's tour guide, we arranged to use Brandon again in Sicily! We went to Mt. Edna, had a fabulous lunch at a local winery & went to the city of Taormina. I highly recommend using "The Roman Guy". We will definitely use him again when we go back in the near future! Mariann
  

[[{'review_date': 'October 22, 2019',
   'review_body': 'Our guide Serena was great and informative. Our only complaint had nothing to do with Serena or The Roman Guy, it was the venue itself. On many photos the colosseum appears well lit during the after hours tour, but it was not. It was difficult to make anything out from the various vantage points that we were at. There was quite a bit of walking and many stairs involved, but we’re chubby and needed the exercise. I can’t fault anyone but the keepers of the colosseum itself for the poor illumination. It did make it a little disappointing, but it was still nice to see what we did with essentially no one around us. I would certainly book with Roman Guy again. If you take any tour, you’ll be lucky to get Serena as a tour guide.',
   'rating': 'bubble_40',
   'review_title': 'Great guide, colosseum was a little underwhelming'},
  {'review_date': 'October 21, 2019',
   'review_body': 'Serena was an exceptional guide for this tour. Very k

In [75]:
df = pd.DataFrame()
review_body=[]
review_date=[]
rating=[]
title=[]
for lst in review_list:
    for item in lst: 
        review_date.append(item['review_date'])
        title.append(item['review_title'])
        review_body.append(item['review_body'])
        rating.append(item['rating'])
df['date'] = review_date
df['title'] = title
df['review'] = review_body
df['rating'] = rating

# clean rating
clean_rating = []
for row in df['rating']:
    row = str(row)
    row = re.findall('\d', row)
    if len(row)>0: 
        row = row[0]
    else:
        row = np.nan
    clean_rating.append(row)
df['rating'] = clean_rating
df

date                                              title  \
0       October 22, 2019  Great guide, colosseum was a little underwhelming   
1       October 21, 2019            Night tour of Colosseum and Underground   
2       October 21, 2019                          Versailles & Louvre tours   
3       October 21, 2019                                            Superb!   
4       October 21, 2019                                 Tour of a Lifetime   
5       October 21, 2019                                          Excellent   
6       October 20, 2019                                        Great tour!   
7       October 20, 2019                                     Good way to go   
8       October 20, 2019  Detailed Itinerary, Vatican, Sistine and St.Pe...   
9       October 20, 2019                        Ohhhhhhhh what a night!!!!!   
10      October 20, 2019  Colosseum Underground Tour with Roman Forum an...   
11      October 20, 2019                                Great day, but busy   
12      October 20, 2019                            Great tour, great guide   
13      October 20, 2019                                    Incredible Tour   
14      October 20, 2019                                           Fabulous   
15      October 19, 2019                                 Vatican night tour   
16      October 19, 2019  Great tour of the Colosseum, Palantine Hill an...   
17      October 19, 2019  Early entry is a MUST!!!! Great way to see eve...   
18      October 19, 2019                                     Wonderful tour   
19      October 19, 2019                               Wonderful experience   
20      October 19, 2019  The Roman Guy is by far the best tour speciali...   
21      October 18, 2019                                 Amazing Experience   
22      October 18, 2019           A Great Way to see Michelangelo’s David!   
23      October 18, 2019  Did the Vatican early morning tour, crowded an...   
24      October 17, 2019                      1/2 day tour of Rome on Ebike   
25      October 17, 2019                          FANTASTIC! The best tour!   
26      October 17, 2019                            Privilege Vatican tour    
27      October 17, 2019                                     Colosseum tour   
28      October 16, 2019                        Overwhelming in a good way!   
29      October 15, 2019                          Paris Guy tour Versailles   
...                  ...                                                ...   
4180      April 12, 2013                          The Roman Guy -- a must!!   
4181       March 6, 2013                                        great guide   
4182   February 19, 2013  It's like having a friend show you around thei...   
4183   February 19, 2013  Great and knowledgable tour guide in Brandon--...   
4184     January 8, 2013  Best decision ever...contacting and using the ...   
4185     January 4, 2013  "Easy..Exciting..Entertaining..Enjoyable and E...   
4186   November 22, 2012            Great experiences with Sean and Brandon   
4187   November 12, 2012                                   Made life simple   
4188   November 11, 2012              Knowledge and humor - molto rispetto!   
4189    November 6, 2012                       Best way to experience Rome!   
4190    October 23, 2012                      Private Tour of the Colesseum   
4191    October 20, 2012                                Excellent for sure!   
4192    October 14, 2012                                 Unexpected and fun   
4193    October 12, 2012  The Forum & the Catacombs: Top notch! Brandon ...   
4194    October 10, 2012      This is the perfect way to experience Rome...   
4195     October 2, 2012                 Best travel planner and tour guide   
4196     October 1, 2012                         The Best of Rome & Sicily!   
4197     October 1, 2012  Brandon is very enjoyable and seems to have re...   
4198  September 27, 2012                                       Walking

In [80]:
df.to_csv('tripadvisor_reviews.csv', index=False)